## Немного о датасете:
Данный датасет показывает определение пола человека исходя из данных его речи. С помощью методов классификации - мы обучим модель определять принадлежность человека к одному из двух гендеров: Мужчина или женщина

In [1]:
import pandas as pd
import xgboost as xgb
from sklearn.metrics import *
from sklearn.ensemble import  GradientBoostingClassifier
from lightgbm import LGBMClassifier
from catboost import CatBoostClassifier 
from xgboost import XGBClassifier
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler, OneHotEncoder,LabelEncoder


In [2]:
data = pd.read_csv('voice.csv',sep = ',')


In [3]:
data.head()

meanfreq        sd    median       Q25       Q75       IQR       skew  \
0  0.059781  0.064241  0.032027  0.015071  0.090193  0.075122  12.863462   
1  0.066009  0.067310  0.040229  0.019414  0.092666  0.073252  22.423285   
2  0.077316  0.083829  0.036718  0.008701  0.131908  0.123207  30.757155   
3  0.151228  0.072111  0.158011  0.096582  0.207955  0.111374   1.232831   
4  0.135120  0.079146  0.124656  0.078720  0.206045  0.127325   1.101174   

          kurt    sp.ent       sfm  ...  centroid   meanfun    minfun  \
0   274.402906  0.893369  0.491918  ...  0.059781  0.084279  0.015702   
1   634.613855  0.892193  0.513724  ...  0.066009  0.107937  0.015826   
2  1024.927705  0.846389  0.478905  ...  0.077316  0.098706  0.015656   
3     4.177296  0.963322  0.727232  ...  0.151228  0.088965  0.017798   
4     4.333713  0.971955  0.783568  ...  0.135120  0.106398  0.016931   

     maxfun   meandom    mindom    maxdom   dfrange   modindx  label  
0  0.275862  0.007812  0.007812  0.007812  0.000000  0.000000   male  
1  0.250000  0.009014  0.007812  0.054688  0.046875  0.052632   male  
2  0.271186  0.007990  0.007812  0.015625  0.007812  0.046512   male  
3  0.250000  0.201497  0.007812  0.562500  0.554688  0.247119   male  
4  0.266667  0.712812  0.007812  5.484375  5.476562  0.208274   male  

[5 rows x 21 columns]

In [4]:
data['label'].value_counts()

male      1584
female    1584
Name: label, dtype: int64

In [5]:
data = data.dropna()

In [6]:
data.head()

meanfreq        sd    median       Q25       Q75       IQR       skew  \
0  0.059781  0.064241  0.032027  0.015071  0.090193  0.075122  12.863462   
1  0.066009  0.067310  0.040229  0.019414  0.092666  0.073252  22.423285   
2  0.077316  0.083829  0.036718  0.008701  0.131908  0.123207  30.757155   
3  0.151228  0.072111  0.158011  0.096582  0.207955  0.111374   1.232831   
4  0.135120  0.079146  0.124656  0.078720  0.206045  0.127325   1.101174   

          kurt    sp.ent       sfm  ...  centroid   meanfun    minfun  \
0   274.402906  0.893369  0.491918  ...  0.059781  0.084279  0.015702   
1   634.613855  0.892193  0.513724  ...  0.066009  0.107937  0.015826   
2  1024.927705  0.846389  0.478905  ...  0.077316  0.098706  0.015656   
3     4.177296  0.963322  0.727232  ...  0.151228  0.088965  0.017798   
4     4.333713  0.971955  0.783568  ...  0.135120  0.106398  0.016931   

     maxfun   meandom    mindom    maxdom   dfrange   modindx  label  
0  0.275862  0.007812  0.007812  0.007812  0.000000  0.000000   male  
1  0.250000  0.009014  0.007812  0.054688  0.046875  0.052632   male  
2  0.271186  0.007990  0.007812  0.015625  0.007812  0.046512   male  
3  0.250000  0.201497  0.007812  0.562500  0.554688  0.247119   male  
4  0.266667  0.712812  0.007812  5.484375  5.476562  0.208274   male  

[5 rows x 21 columns]

## Преобразование данных
Категориальные данные мы преобразуем с помощью LabelEncoder, так как у нас только один бинарный признак
Числовые признаки мы преобразуем с помощью StandardScaler

In [11]:
columns = data.columns.values.tolist ()
columns

['meanfreq',
 'sd',
 'median',
 'Q25',
 'Q75',
 'IQR',
 'skew',
 'kurt',
 'sp.ent',
 'sfm',
 'mode',
 'centroid',
 'meanfun',
 'minfun',
 'maxfun',
 'meandom',
 'mindom',
 'maxdom',
 'dfrange',
 'modindx',
 'label']

In [16]:
numerical_features = ['meanfreq', 'sd', 'median', 'Q25', 'Q75', 'IQR', 'skew', 'kurt', 'sp.ent', 'sfm', 'mode', 'centroid',
 'meanfun', 'minfun', 'maxfun', 'meandom', 'mindom', 'maxdom', 'dfrange', 'modindx']

categorial_features = ['label']

In [17]:
data_train, data_test = train_test_split(data, test_size=0.2, stratify=data['label'])


In [19]:
y_train

1255      male
2262    female
2415    female
1510      male
2899    female
         ...  
1101      male
2541    female
2673    female
1077      male
134       male
Name: label, Length: 2534, dtype: object

In [20]:
scaler = StandardScaler()

In [21]:
data_train_scaled = scaler.fit_transform(data_train[numerical_features])
data_train_scaled[:10]

array([[-0.0398428 ,  0.081114  ,  0.36002101, -0.43388652,  0.31309633,
         0.66691176, -0.30510539, -0.22693776,  0.11494629, -0.15015534,
        -0.62582612, -0.0398428 , -0.74141136,  0.61656549,  0.31868414,
         0.81928708, -0.45898628,  0.4606154 ,  0.46895187, -0.68321185],
       [-2.32866968,  0.90885834, -2.33546279, -1.89528371, -2.44828849,
         0.79960766, -0.45373399, -0.24021023,  1.55980049,  1.95105756,
        -0.01348015, -2.32866968,  0.54548366, -0.07709652,  0.26924992,
        -0.93039812, -0.70673933, -1.11958344, -1.10718879,  0.96603655],
       [ 1.23799591, -0.90555679,  0.77364649,  1.12094525,  1.12057089,
        -0.65428294, -0.32552421, -0.23161877, -0.6591328 , -0.82030451,
         0.54873985,  1.23799591,  1.0493601 ,  0.63457542,  0.68081854,
         0.45193977, -0.45898628,  1.07316439,  1.0816488 , -0.75243975],
       [-1.51535115,  1.28141497, -1.85832869, -0.9643798 , -0.39311031,
         0.87913272,  1.27235994,  0.80691535,  

In [23]:
le = LabelEncoder()
data_train_le = le.fit_transform(data_train[categorial_features])
data_train_le[:10]

C:\Users\spostroumov\Anaconda3\lib\site-packages\sklearn\utils\validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


array([1, 0, 0, 1, 0, 1, 1, 0, 1, 1])

In [28]:
data_train_tramsformed = pd.concat([pd.DataFrame(data_train_scaled, columns=numerical_features),
                                    pd.DataFrame(data_train_le, columns=categorial_features),
                                   ], axis=1)
data_train_tramsformed.head()

meanfreq        sd    median       Q25       Q75       IQR      skew  \
0 -0.039843  0.081114  0.360021 -0.433887  0.313096  0.666912 -0.305105   
1 -2.328670  0.908858 -2.335463 -1.895284 -2.448288  0.799608 -0.453734   
2  1.237996 -0.905557  0.773646  1.120945  1.120571 -0.654283 -0.325524   
3 -1.515351  1.281415 -1.858329 -0.964380 -0.393110  0.879133  1.272360   
4  1.122325  0.052414  1.132862  1.200063  1.269109 -0.661998 -0.337089   

       kurt    sp.ent       sfm  ...  centroid   meanfun    minfun    maxfun  \
0 -0.226938  0.114946 -0.150155  ... -0.039843 -0.741411  0.616565  0.318684   
1 -0.240210  1.559800  1.951058  ... -2.328670  0.545484 -0.077097  0.269250   
2 -0.231619 -0.659133 -0.820305  ...  1.237996  1.049360  0.634575  0.680819   
3  0.806915  0.604923  0.979420  ... -1.515351 -1.486955 -1.090363 -2.104798   
4 -0.234264 -0.043371 -0.088530  ...  1.122325  0.881535  0.611466  0.680819   

    meandom    mindom    maxdom   dfrange   modindx  label  
0  0.819287 -0.458986  0.460615  0.468952 -0.683212      1  
1 -0.930398 -0.706739 -1.119583 -1.107189  0.966037      0  
2  0.451940 -0.458986  1.073164  1.081649 -0.752440      0  
3 -1.441361 -0.706739 -1.290476 -1.278122 -0.198826      1  
4  0.127115 -0.458986  0.134366  0.142624 -0.418384      0  

[5 rows x 21 columns]

In [31]:
X_train = data_train_tramsformed.drop('label', axis = 1)
y_train = data_train_tramsformed['label']

#X_test = data_test.drop('label', axis = 1)
#y_test = data_test['label']

## Обучение без гиперпараметров

In [30]:
clf_cb = CatBoostClassifier()
reg = GradientBoostingClassifier() ## Из коробки

clf = LGBMClassifier()

xgb = XGBClassifier()

In [35]:
clf_cb.fit(X_train,y_train)
reg.fit(X_train,y_train)
clf.fit(X_train,y_train)
xgb.fit(X_train,y_train)

Learning rate set to 0.015324
0:	learn: 0.6628767	total: 3.24ms	remaining: 3.23s
1:	learn: 0.6337257	total: 6.14ms	remaining: 3.06s
2:	learn: 0.6077835	total: 8.77ms	remaining: 2.92s
3:	learn: 0.5825327	total: 11.4ms	remaining: 2.85s
4:	learn: 0.5564841	total: 14ms	remaining: 2.78s
5:	learn: 0.5385385	total: 16.4ms	remaining: 2.71s
6:	learn: 0.5152506	total: 18.9ms	remaining: 2.67s
7:	learn: 0.4924713	total: 21.2ms	remaining: 2.62s
8:	learn: 0.4729074	total: 23.6ms	remaining: 2.6s
9:	learn: 0.4531159	total: 25.9ms	remaining: 2.56s
10:	learn: 0.4331841	total: 28.1ms	remaining: 2.53s
11:	learn: 0.4159752	total: 30.4ms	remaining: 2.5s
12:	learn: 0.4004552	total: 32.6ms	remaining: 2.48s
13:	learn: 0.3858272	total: 34.8ms	remaining: 2.45s
14:	learn: 0.3711883	total: 37.1ms	remaining: 2.43s
15:	learn: 0.3581331	total: 39.5ms	remaining: 2.43s
16:	learn: 0.3492361	total: 41.9ms	remaining: 2.42s
17:	learn: 0.3364363	total: 44.1ms	remaining: 2.41s
18:	learn: 0.3255636	total: 46.4ms	remaining: 2.

229:	learn: 0.0397561	total: 534ms	remaining: 1.79s
230:	learn: 0.0396409	total: 537ms	remaining: 1.79s
231:	learn: 0.0396095	total: 540ms	remaining: 1.79s
232:	learn: 0.0394504	total: 543ms	remaining: 1.79s
233:	learn: 0.0393988	total: 547ms	remaining: 1.79s
234:	learn: 0.0392306	total: 550ms	remaining: 1.79s
235:	learn: 0.0390457	total: 553ms	remaining: 1.79s
236:	learn: 0.0388986	total: 556ms	remaining: 1.79s
237:	learn: 0.0387438	total: 559ms	remaining: 1.79s
238:	learn: 0.0386348	total: 562ms	remaining: 1.79s
239:	learn: 0.0385299	total: 564ms	remaining: 1.79s
240:	learn: 0.0384545	total: 567ms	remaining: 1.79s
241:	learn: 0.0384046	total: 570ms	remaining: 1.79s
242:	learn: 0.0382942	total: 573ms	remaining: 1.78s
243:	learn: 0.0382063	total: 576ms	remaining: 1.78s
244:	learn: 0.0381535	total: 578ms	remaining: 1.78s
245:	learn: 0.0380286	total: 582ms	remaining: 1.78s
246:	learn: 0.0378948	total: 584ms	remaining: 1.78s
247:	learn: 0.0377084	total: 587ms	remaining: 1.78s
248:	learn: 

428:	learn: 0.0243940	total: 1.08s	remaining: 1.43s
429:	learn: 0.0243538	total: 1.08s	remaining: 1.43s
430:	learn: 0.0243038	total: 1.08s	remaining: 1.43s
431:	learn: 0.0242694	total: 1.08s	remaining: 1.43s
432:	learn: 0.0242103	total: 1.09s	remaining: 1.43s
433:	learn: 0.0240962	total: 1.09s	remaining: 1.42s
434:	learn: 0.0239938	total: 1.09s	remaining: 1.42s
435:	learn: 0.0239093	total: 1.09s	remaining: 1.42s
436:	learn: 0.0238470	total: 1.1s	remaining: 1.41s
437:	learn: 0.0238056	total: 1.1s	remaining: 1.41s
438:	learn: 0.0237907	total: 1.1s	remaining: 1.41s
439:	learn: 0.0237333	total: 1.11s	remaining: 1.41s
440:	learn: 0.0237076	total: 1.11s	remaining: 1.41s
441:	learn: 0.0236882	total: 1.11s	remaining: 1.4s
442:	learn: 0.0236620	total: 1.11s	remaining: 1.4s
443:	learn: 0.0235870	total: 1.12s	remaining: 1.4s
444:	learn: 0.0235211	total: 1.12s	remaining: 1.4s
445:	learn: 0.0234951	total: 1.12s	remaining: 1.39s
446:	learn: 0.0234505	total: 1.12s	remaining: 1.39s
447:	learn: 0.02334

640:	learn: 0.0156571	total: 1.61s	remaining: 903ms
641:	learn: 0.0156454	total: 1.61s	remaining: 901ms
642:	learn: 0.0156365	total: 1.62s	remaining: 898ms
643:	learn: 0.0156268	total: 1.62s	remaining: 896ms
644:	learn: 0.0155809	total: 1.62s	remaining: 894ms
645:	learn: 0.0155587	total: 1.63s	remaining: 892ms
646:	learn: 0.0154634	total: 1.63s	remaining: 890ms
647:	learn: 0.0154425	total: 1.63s	remaining: 888ms
648:	learn: 0.0154289	total: 1.64s	remaining: 885ms
649:	learn: 0.0153963	total: 1.64s	remaining: 883ms
650:	learn: 0.0153692	total: 1.64s	remaining: 881ms
651:	learn: 0.0153286	total: 1.65s	remaining: 879ms
652:	learn: 0.0153194	total: 1.65s	remaining: 877ms
653:	learn: 0.0153009	total: 1.65s	remaining: 875ms
654:	learn: 0.0152860	total: 1.66s	remaining: 873ms
655:	learn: 0.0152727	total: 1.66s	remaining: 870ms
656:	learn: 0.0152566	total: 1.68s	remaining: 876ms
657:	learn: 0.0151671	total: 1.68s	remaining: 873ms
658:	learn: 0.0151595	total: 1.68s	remaining: 871ms
659:	learn: 

817:	learn: 0.0117205	total: 2.14s	remaining: 476ms
818:	learn: 0.0117012	total: 2.14s	remaining: 473ms
819:	learn: 0.0116855	total: 2.14s	remaining: 471ms
820:	learn: 0.0116518	total: 2.15s	remaining: 468ms
821:	learn: 0.0116430	total: 2.15s	remaining: 465ms
822:	learn: 0.0116372	total: 2.15s	remaining: 463ms
823:	learn: 0.0116295	total: 2.15s	remaining: 460ms
824:	learn: 0.0115814	total: 2.16s	remaining: 458ms
825:	learn: 0.0115771	total: 2.16s	remaining: 455ms
826:	learn: 0.0115617	total: 2.16s	remaining: 453ms
827:	learn: 0.0115222	total: 2.17s	remaining: 450ms
828:	learn: 0.0115042	total: 2.17s	remaining: 448ms
829:	learn: 0.0114730	total: 2.17s	remaining: 445ms
830:	learn: 0.0114713	total: 2.17s	remaining: 442ms
831:	learn: 0.0114545	total: 2.18s	remaining: 440ms
832:	learn: 0.0114508	total: 2.18s	remaining: 437ms
833:	learn: 0.0114429	total: 2.18s	remaining: 435ms
834:	learn: 0.0114412	total: 2.19s	remaining: 432ms
835:	learn: 0.0114247	total: 2.19s	remaining: 430ms
836:	learn: 

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=None, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=None, gpu_id=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=None, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=None, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              n_estimators=100, n_jobs=None, num_parallel_tree=None,
              predictor=None, random_state=None, ...)

In [36]:
data_test_scaled = scaler.transform(data_test[numerical_features])
data_test_le = le.transform(data_test[categorial_features])


C:\Users\spostroumov\Anaconda3\lib\site-packages\sklearn\utils\validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


In [37]:
data_test_tramsformed = pd.concat([pd.DataFrame(data_test_scaled, columns=numerical_features),
                                    pd.DataFrame(data_test_le, columns=categorial_features),
                                   ], axis=1)
data_test_tramsformed.head()

meanfreq        sd    median       Q25       Q75       IQR      skew  \
0  0.246989 -1.141496 -0.040356  0.599940 -0.287294 -0.841487 -0.169927   
1 -0.959140  0.274870 -0.810989 -0.852244 -1.005942  0.412158 -0.003744   
2  0.937543 -1.464664  0.657070  1.060596  0.182965 -1.104962 -0.158280   
3 -0.069641  0.228755 -0.072146 -0.286292 -0.206399  0.211303 -0.322526   
4  0.188361  0.071004  0.239556 -0.205811  0.538085  0.532119 -0.324943   

       kurt    sp.ent       sfm  ...  centroid   meanfun    minfun    maxfun  \
0 -0.204698 -0.629843 -0.728729  ...  0.246989  0.926568  0.320977 -1.205538   
1 -0.157174  0.460203  0.635232  ... -0.959140 -1.632300  0.515985 -4.808712   
2 -0.188588 -0.703959 -1.286291  ...  0.937543  1.152457  0.551842  0.680819   
3 -0.224629  0.566037  0.500760  ... -0.069641 -0.889262  0.554270  0.680819   
4 -0.218797  0.478039 -0.097090  ...  0.188361 -0.718641  0.561583  0.627291   

    meandom    mindom    maxdom   dfrange   modindx  label  
0 -0.581356  1.646915  0.081101  0.051608 -0.461333      0  
1 -0.567083  0.408149 -1.223617 -1.231227  1.574831      1  
2  0.406861 -0.458986  1.439362  1.447935 -0.881995      0  
3  0.677825 -0.458986 -0.185224 -0.177044 -0.344059      1  
4 -0.617820 -0.458986 -0.591371 -0.583289 -0.572855      1  

[5 rows x 21 columns]

In [40]:
print ('Train CatBoostClassifier ROC-AUC =', roc_auc_score(y_train, clf_cb.predict_proba(X_train)[:,1]))
print ('Test CatBoostClassifier ROC-AUC = ', roc_auc_score(y_test, clf_cb.predict_proba(X_test)[:,1]))

print ('Train GradientBoostingClassifier ROC-AUC =', roc_auc_score(y_train, reg.predict_proba(X_train)[:,1]))
print ('Test GradientBoostingClassifier ROC-AUC = ', roc_auc_score(y_test, reg.predict_proba(X_test)[:,1]))

print ('Train LGBMClassifier ROC-AUC =', roc_auc_score(y_train, clf.predict_proba(X_train)[:,1]))
print ('Test LGBMClassifier ROC-AUC = ', roc_auc_score(y_test, clf.predict_proba(X_test)[:,1]))


print ('Train XGBClassifier ROC-AUC =', roc_auc_score(y_train, xgb.predict_proba(X_train)[:,1]))
print ('Test XGBClassifier ROC-AUC = ', roc_auc_score(y_test, xgb.predict_proba(X_test)[:,1]))


Train CatBoostClassifier ROC-AUC = 1.0
Test CatBoostClassifier ROC-AUC =  0.7543014658320811
Train GradientBoostingClassifier ROC-AUC = 0.9999526564998577
Test GradientBoostingClassifier ROC-AUC =  0.7811999323309019
Train LGBMClassifier ROC-AUC = 1.0
Test LGBMClassifier ROC-AUC =  0.5030451094149608
Train XGBClassifier ROC-AUC = 1.0
Test XGBClassifier ROC-AUC =  0.5720178327976196


## Результаты обучения без гиперпараметров:
После тестирования классификаторов со значениями гиперпараметров по умолчанию лидирует GradientBoostingClassifier  с показателем roc_auc_score =  0.78

## Используем гиперпараметры

In [41]:
!pip3 install optuna

In [46]:
import optuna

In [ ]:
def objective(trial):
    """Define the objective function"""

    params = {
        'max_depth': trial.suggest_int('max_depth', 1, 9),
        'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 1.0),
        'n_estimators': trial.suggest_int('n_estimators', 50, 500),
        'subsample': trial.suggest_loguniform('subsample', 0.01, 1.0)
    }

    # Fit the model
    optuna_model =LGBMClassifier(**params)
    optuna_model.fit(X_train, y_train)

    # Make predictions
    y_pred = optuna_model.predict(X_test)

    # Evaluate predictions
    roc_auc = roc_auc_score(y_test, y_pred)
    return roc_auc

In [62]:
study_LGBMClassifier = optuna.create_study(direction='maximize')


[I 2023-08-13 13:44:17,341] A new study created in memory with name: no-name-f8b5ffe0-2882-4ef6-a878-d67866c521fd


In [63]:
study_LGBMClassifier.optimize(objective, n_trials=100)


<ipython-input-61-e0990160658d>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 1.0),
<ipython-input-61-e0990160658d>:8: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'subsample': trial.suggest_loguniform('subsample', 0.01, 1.0)
[I 2023-08-13 13:44:19,066] Trial 0 finished with value: 0.5536277602523659 and parameters: {'max_depth': 6, 'learning_rate': 0.014138863481908489, 'n_estimators': 398, 'subsample': 0.27352417007238095}. Best is trial 0 with value: 0.5536277602523659.
<ipython-input-61-e0990160658d>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This 

[I 2023-08-13 13:44:20,666] Trial 9 finished with value: 0.5 and parameters: {'max_depth': 4, 'learning_rate': 0.09422162734470692, 'n_estimators': 230, 'subsample': 0.5108424480827464}. Best is trial 3 with value: 0.5993690851735016.
<ipython-input-61-e0990160658d>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 1.0),
<ipython-input-61-e0990160658d>:8: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'subsample': trial.suggest_loguniform('subsample', 0.01, 1.0)
[I 2023-08-13 13:44:20,782] Trial 10 finished with value: 0.5078864353312303 and parameters: {'max_depth': 9, 'learning_ra

<ipython-input-61-e0990160658d>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 1.0),
<ipython-input-61-e0990160658d>:8: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'subsample': trial.suggest_loguniform('subsample', 0.01, 1.0)
[I 2023-08-13 13:44:22,461] Trial 19 finished with value: 0.5094637223974764 and parameters: {'max_depth': 5, 'learning_rate': 0.05464255936077542, 'n_estimators': 196, 'subsample': 0.5164683041661122}. Best is trial 15 with value: 0.6798107255520505.
<ipython-input-61-e0990160658d>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This 

[I 2023-08-13 13:44:24,430] Trial 28 finished with value: 0.6577287066246057 and parameters: {'max_depth': 9, 'learning_rate': 0.04621361187038237, 'n_estimators': 185, 'subsample': 0.6334866168335737}. Best is trial 15 with value: 0.6798107255520505.
<ipython-input-61-e0990160658d>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 1.0),
<ipython-input-61-e0990160658d>:8: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'subsample': trial.suggest_loguniform('subsample', 0.01, 1.0)
[I 2023-08-13 13:44:24,662] Trial 29 finished with value: 0.5189274447949527 and parameters: {'max_depth'

<ipython-input-61-e0990160658d>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 1.0),
<ipython-input-61-e0990160658d>:8: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'subsample': trial.suggest_loguniform('subsample', 0.01, 1.0)
[I 2023-08-13 13:44:26,576] Trial 38 finished with value: 0.5 and parameters: {'max_depth': 5, 'learning_rate': 0.07246537999746014, 'n_estimators': 320, 'subsample': 0.6578968244854405}. Best is trial 15 with value: 0.6798107255520505.
<ipython-input-61-e0990160658d>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be

...

[I 2023-08-13 13:44:29,553] Trial 56 finished with value: 0.4968454258675079 and parameters: {'max_depth': 6, 'learning_rate': 0.020150667249688902, 'n_estimators': 62, 'subsample': 0.8105825510666573}. Best is trial 52 with value: 0.7381703470031546.
<ipython-input-61-e0990160658d>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 1.0),
<ipython-input-61-e0990160658d>:8: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'subsample': trial.suggest_loguniform('subsample', 0.01, 1.0)
[I 2023-08-13 13:44:29,747] Trial 57 finished with value: 0.4936908517350157 and parameters: {'max_depth'

<ipython-input-61-e0990160658d>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 1.0),
<ipython-input-61-e0990160658d>:8: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'subsample': trial.suggest_loguniform('subsample', 0.01, 1.0)
[I 2023-08-13 13:44:31,053] Trial 66 finished with value: 0.49526813880126186 and parameters: {'max_depth': 7, 'learning_rate': 0.021814704497389217, 'n_estimators': 133, 'subsample': 0.5127075135162309}. Best is trial 52 with value: 0.7381703470031546.
<ipython-input-61-e0990160658d>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. Thi

[I 2023-08-13 13:44:32,263] Trial 75 finished with value: 0.610410094637224 and parameters: {'max_depth': 7, 'learning_rate': 0.03580040389101512, 'n_estimators': 100, 'subsample': 0.9722903356821793}. Best is trial 52 with value: 0.7381703470031546.
<ipython-input-61-e0990160658d>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 1.0),
<ipython-input-61-e0990160658d>:8: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'subsample': trial.suggest_loguniform('subsample', 0.01, 1.0)
[I 2023-08-13 13:44:32,414] Trial 76 finished with value: 0.7145110410094636 and parameters: {'max_depth':

<ipython-input-61-e0990160658d>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 1.0),
<ipython-input-61-e0990160658d>:8: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'subsample': trial.suggest_loguniform('subsample', 0.01, 1.0)
[I 2023-08-13 13:44:33,747] Trial 85 finished with value: 0.6119873817034701 and parameters: {'max_depth': 7, 'learning_rate': 0.026056735872114545, 'n_estimators': 182, 'subsample': 0.49565646918533185}. Best is trial 52 with value: 0.7381703470031546.
<ipython-input-61-e0990160658d>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. Thi

<ipython-input-61-e0990160658d>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 1.0),
<ipython-input-61-e0990160658d>:8: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'subsample': trial.suggest_loguniform('subsample', 0.01, 1.0)
[I 2023-08-13 13:44:35,725] Trial 95 finished with value: 0.6861198738170347 and parameters: {'max_depth': 8, 'learning_rate': 0.031195667730557798, 'n_estimators': 201, 'subsample': 0.7794423574456785}. Best is trial 52 with value: 0.7381703470031546.
<ipython-input-61-e0990160658d>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This

In [81]:
print('Number of finished trials: {}'.format(len(study_LGBMClassifier.trials)))
print('Best trial LGBMClassifier:')
trial = study_LGBMClassifier.best_trial

print('  Value: {}'.format(trial.value))
print('  Params: ')

for key, value in trial.params.items():
    print('    {}: {}'.format(key, value))

Number of finished trials: 100
Best trial LGBMClassifier:
  Value: 0.7381703470031546
  Params: 
    max_depth: 7
    learning_rate: 0.03665179496903868
    n_estimators: 140
    subsample: 0.4591550923591838


In [75]:
def objective(trial):
    """Define the objective function"""

    params = {
        'max_depth': trial.suggest_int('max_depth', 1, 9),
        'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 1.0),
        'n_estimators': trial.suggest_int('n_estimators', 50, 500),
        'subsample': trial.suggest_loguniform('subsample', 0.01, 1.0)
    }

    # Fit the model
    optuna_model =CatBoostClassifier(**params)
    optuna_model.fit(X_train, y_train)

    # Make predictions
    y_pred = optuna_model.predict(X_test)

    # Evaluate predictions
    roc_auc = roc_auc_score(y_test, y_pred)
    return roc_auc

In [76]:
study_CatBoostClassifier = optuna.create_study(direction='maximize')


[I 2023-08-13 13:59:18,677] A new study created in memory with name: no-name-d66c1274-213d-4545-b809-a4fa227cbaa0


In [77]:
study_CatBoostClassifier.optimize(objective, n_trials=100)


<ipython-input-75-de5c804e77b8>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 1.0),
<ipython-input-75-de5c804e77b8>:8: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'subsample': trial.suggest_loguniform('subsample', 0.01, 1.0)


0:	learn: 0.6711815	total: 1.79ms	remaining: 312ms
1:	learn: 0.6500739	total: 3.74ms	remaining: 324ms
2:	learn: 0.6240610	total: 5.5ms	remaining: 316ms
3:	learn: 0.6039583	total: 7.11ms	remaining: 304ms
4:	learn: 0.5840660	total: 8.85ms	remaining: 301ms
5:	learn: 0.5665186	total: 10.5ms	remaining: 297ms
6:	learn: 0.5497604	total: 12.1ms	remaining: 291ms
7:	learn: 0.5272901	total: 13.8ms	remaining: 288ms
8:	learn: 0.5065262	total: 15.4ms	remaining: 284ms
9:	learn: 0.4930564	total: 17.1ms	remaining: 282ms
10:	learn: 0.4794165	total: 18.8ms	remaining: 281ms
11:	learn: 0.4612652	total: 20.5ms	remaining: 278ms
12:	learn: 0.4458880	total: 22.1ms	remaining: 276ms
13:	learn: 0.4319281	total: 23.8ms	remaining: 274ms
14:	learn: 0.4161980	total: 25.6ms	remaining: 273ms
15:	learn: 0.4011154	total: 27.2ms	remaining: 270ms
16:	learn: 0.3911318	total: 28.8ms	remaining: 268ms
17:	learn: 0.3774128	total: 30.6ms	remaining: 267ms
18:	learn: 0.3643160	total: 32.3ms	remaining: 265ms
19:	learn: 0.3562170	to

[I 2023-08-13 13:59:20,668] Trial 0 finished with value: 0.5 and parameters: {'max_depth': 2, 'learning_rate': 0.01601733731536742, 'n_estimators': 175, 'subsample': 0.1129700342169696}. Best is trial 0 with value: 0.5.
<ipython-input-75-de5c804e77b8>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 1.0),
<ipython-input-75-de5c804e77b8>:8: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'subsample': trial.suggest_loguniform('subsample', 0.01, 1.0)


0:	learn: 0.2072370	total: 30.4ms	remaining: 7.9s
1:	learn: 0.1240292	total: 36.2ms	remaining: 4.69s
2:	learn: 0.1061058	total: 43ms	remaining: 3.7s
3:	learn: 0.0845236	total: 49.1ms	remaining: 3.15s
4:	learn: 0.0807322	total: 56.6ms	remaining: 2.9s
5:	learn: 0.0759187	total: 62.7ms	remaining: 2.67s
6:	learn: 0.0741294	total: 69.2ms	remaining: 2.51s
7:	learn: 0.0701435	total: 76.8ms	remaining: 2.43s
8:	learn: 0.0638007	total: 83.2ms	remaining: 2.33s
9:	learn: 0.0622028	total: 89.7ms	remaining: 2.25s
10:	learn: 0.0591655	total: 95.4ms	remaining: 2.17s
11:	learn: 0.0578472	total: 102ms	remaining: 2.12s
12:	learn: 0.0540086	total: 110ms	remaining: 2.09s
13:	learn: 0.0525445	total: 115ms	remaining: 2.03s
14:	learn: 0.0515883	total: 121ms	remaining: 1.99s
15:	learn: 0.0500377	total: 128ms	remaining: 1.96s
16:	learn: 0.0488037	total: 134ms	remaining: 1.93s
17:	learn: 0.0466897	total: 142ms	remaining: 1.91s
18:	learn: 0.0458989	total: 148ms	remaining: 1.88s
19:	learn: 0.0443369	total: 155ms	r

177:	learn: 0.0038253	total: 1.12s	remaining: 524ms
178:	learn: 0.0037612	total: 1.13s	remaining: 519ms
179:	learn: 0.0037612	total: 1.14s	remaining: 512ms
180:	learn: 0.0037612	total: 1.14s	remaining: 506ms
181:	learn: 0.0037612	total: 1.15s	remaining: 499ms
182:	learn: 0.0037612	total: 1.16s	remaining: 492ms
183:	learn: 0.0037612	total: 1.16s	remaining: 486ms
184:	learn: 0.0037612	total: 1.17s	remaining: 479ms
185:	learn: 0.0037612	total: 1.17s	remaining: 473ms
186:	learn: 0.0037611	total: 1.18s	remaining: 466ms
187:	learn: 0.0037610	total: 1.18s	remaining: 460ms
188:	learn: 0.0037610	total: 1.19s	remaining: 453ms
189:	learn: 0.0037609	total: 1.2s	remaining: 447ms
190:	learn: 0.0037609	total: 1.2s	remaining: 441ms
191:	learn: 0.0037608	total: 1.21s	remaining: 435ms
192:	learn: 0.0037608	total: 1.22s	remaining: 428ms
193:	learn: 0.0037608	total: 1.22s	remaining: 422ms
194:	learn: 0.0037608	total: 1.23s	remaining: 415ms
195:	learn: 0.0037607	total: 1.23s	remaining: 409ms
196:	learn: 0.

...

[I 2023-08-13 14:02:49,886] Trial 98 finished with value: 0.4810725552050473 and parameters: {'max_depth': 9, 'learning_rate': 0.1410481295883535, 'n_estimators': 210, 'subsample': 0.02278796420049946}. Best is trial 29 with value: 0.7965299684542586.


200:	learn: 0.0028557	total: 2.74s	remaining: 123ms
201:	learn: 0.0028260	total: 2.75s	remaining: 109ms
202:	learn: 0.0028260	total: 2.76s	remaining: 95.3ms
203:	learn: 0.0027953	total: 2.78s	remaining: 81.7ms
204:	learn: 0.0027720	total: 2.79s	remaining: 68ms
205:	learn: 0.0027720	total: 2.8s	remaining: 54.4ms
206:	learn: 0.0027704	total: 2.82s	remaining: 40.8ms
207:	learn: 0.0027339	total: 2.83s	remaining: 27.2ms
208:	learn: 0.0027180	total: 2.84s	remaining: 13.6ms
209:	learn: 0.0026957	total: 2.86s	remaining: 0us


<ipython-input-75-de5c804e77b8>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 1.0),
<ipython-input-75-de5c804e77b8>:8: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'subsample': trial.suggest_loguniform('subsample', 0.01, 1.0)


0:	learn: 0.2811704	total: 13.7ms	remaining: 1.42s
1:	learn: 0.1849383	total: 15.3ms	remaining: 780ms
2:	learn: 0.1269778	total: 16.7ms	remaining: 563ms
3:	learn: 0.1113504	total: 18.1ms	remaining: 453ms
4:	learn: 0.0931009	total: 19.5ms	remaining: 386ms
5:	learn: 0.0876438	total: 20.9ms	remaining: 341ms
6:	learn: 0.0840969	total: 22.2ms	remaining: 308ms
7:	learn: 0.0811138	total: 23.6ms	remaining: 283ms
8:	learn: 0.0787701	total: 24.9ms	remaining: 263ms
9:	learn: 0.0782900	total: 26.4ms	remaining: 248ms
10:	learn: 0.0755202	total: 28ms	remaining: 237ms
11:	learn: 0.0732103	total: 29.4ms	remaining: 226ms
12:	learn: 0.0727421	total: 30.9ms	remaining: 216ms
13:	learn: 0.0716487	total: 32.4ms	remaining: 209ms
14:	learn: 0.0689121	total: 33.9ms	remaining: 201ms
15:	learn: 0.0686537	total: 35.4ms	remaining: 195ms
16:	learn: 0.0664749	total: 36.8ms	remaining: 188ms
17:	learn: 0.0653585	total: 38.2ms	remaining: 182ms
18:	learn: 0.0635475	total: 39.7ms	remaining: 178ms
19:	learn: 0.0620852	tot

[I 2023-08-13 14:02:50,198] Trial 99 finished with value: 0.3533123028391167 and parameters: {'max_depth': 4, 'learning_rate': 0.46156425907833637, 'n_estimators': 104, 'subsample': 0.025552739755568307}. Best is trial 29 with value: 0.7965299684542586.


In [80]:
print('Number of finished trials: {}'.format(len(study_CatBoostClassifier.trials)))
print('Best trial CatBoostClassifier:')
trial = study_CatBoostClassifier.best_trial

print('  Value: {}'.format(trial.value))
print('  Params: ')

for key, value in trial.params.items():
    print('    {}: {}'.format(key, value))

Number of finished trials: 100
Best trial CatBoostClassifier:
  Value: 0.7965299684542586
  Params: 
    max_depth: 9
    learning_rate: 0.20918584150421557
    n_estimators: 161
    subsample: 0.02428918243391573


In [70]:
def objective(trial):
    """Define the objective function"""

    params = {
        'max_depth': trial.suggest_int('max_depth', 1, 9),
        'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 1.0),
        'n_estimators': trial.suggest_int('n_estimators', 50, 500),
        'subsample': trial.suggest_loguniform('subsample', 0.01, 1.0)
    }

    # Fit the model
    optuna_model =GradientBoostingClassifier(**params)
    optuna_model.fit(X_train, y_train)

    # Make predictions
    y_pred = optuna_model.predict(X_test)

    # Evaluate predictions
    roc_auc = roc_auc_score(y_test, y_pred)
    return roc_auc

In [82]:
study_GradientBoostingClassifier = optuna.create_study(direction='maximize')
study_GradientBoostingClassifier.optimize(objective, n_trials=100)

print('Number of finished trials: {}'.format(len(study_GradientBoostingClassifier.trials)))
print('Best trial GradientBoostingClassifier:')
trial = study_GradientBoostingClassifier.best_trial

print('  Value: {}'.format(trial.value))
print('  Params: ')

for key, value in trial.params.items():
    print('    {}: {}'.format(key, value))

[I 2023-08-13 14:04:30,697] A new study created in memory with name: no-name-77b192be-8173-4e32-84e9-0ff7b2c7d9f3
<ipython-input-75-de5c804e77b8>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 1.0),
<ipython-input-75-de5c804e77b8>:8: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'subsample': trial.suggest_loguniform('subsample', 0.01, 1.0)


0:	learn: 0.2419432	total: 4.76ms	remaining: 1.55s
1:	learn: 0.1474556	total: 9.46ms	remaining: 1.54s
2:	learn: 0.1096701	total: 13.1ms	remaining: 1.42s
3:	learn: 0.0914091	total: 16.6ms	remaining: 1.34s
4:	learn: 0.0808501	total: 20.1ms	remaining: 1.29s
5:	learn: 0.0753534	total: 23.5ms	remaining: 1.26s
6:	learn: 0.0705858	total: 26.8ms	remaining: 1.23s
7:	learn: 0.0684956	total: 30.6ms	remaining: 1.22s
8:	learn: 0.0579508	total: 34.2ms	remaining: 1.21s
9:	learn: 0.0490784	total: 37.7ms	remaining: 1.2s
10:	learn: 0.0466268	total: 41.2ms	remaining: 1.18s
11:	learn: 0.0440558	total: 44.6ms	remaining: 1.17s
12:	learn: 0.0406978	total: 48.2ms	remaining: 1.16s
13:	learn: 0.0373047	total: 51.8ms	remaining: 1.16s
14:	learn: 0.0327897	total: 55.3ms	remaining: 1.15s
15:	learn: 0.0310908	total: 59ms	remaining: 1.15s
16:	learn: 0.0293904	total: 62.6ms	remaining: 1.14s
17:	learn: 0.0280063	total: 66.2ms	remaining: 1.14s
18:	learn: 0.0269520	total: 69.7ms	remaining: 1.13s
19:	learn: 0.0261919	tota

180:	learn: 0.0013735	total: 586ms	remaining: 473ms
181:	learn: 0.0013735	total: 590ms	remaining: 470ms
182:	learn: 0.0013735	total: 593ms	remaining: 467ms
183:	learn: 0.0013735	total: 597ms	remaining: 464ms
184:	learn: 0.0013735	total: 600ms	remaining: 461ms
185:	learn: 0.0013734	total: 604ms	remaining: 458ms
186:	learn: 0.0013734	total: 608ms	remaining: 455ms
187:	learn: 0.0013732	total: 611ms	remaining: 452ms
188:	learn: 0.0013729	total: 614ms	remaining: 448ms
189:	learn: 0.0013729	total: 617ms	remaining: 445ms
190:	learn: 0.0013303	total: 620ms	remaining: 442ms
191:	learn: 0.0013302	total: 623ms	remaining: 438ms
192:	learn: 0.0013302	total: 626ms	remaining: 435ms
193:	learn: 0.0013294	total: 629ms	remaining: 431ms
194:	learn: 0.0013294	total: 632ms	remaining: 428ms
195:	learn: 0.0013289	total: 635ms	remaining: 424ms
196:	learn: 0.0013289	total: 638ms	remaining: 421ms
197:	learn: 0.0013288	total: 641ms	remaining: 418ms
198:	learn: 0.0013288	total: 644ms	remaining: 414ms
199:	learn: 

[I 2023-08-13 14:04:31,986] Trial 0 finished with value: 0.3675078864353313 and parameters: {'max_depth': 7, 'learning_rate': 0.5260530527778136, 'n_estimators': 327, 'subsample': 0.02168925184334622}. Best is trial 0 with value: 0.3675078864353313.
<ipython-input-75-de5c804e77b8>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 1.0),
<ipython-input-75-de5c804e77b8>:8: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'subsample': trial.suggest_loguniform('subsample', 0.01, 1.0)


0:	learn: 0.6433853	total: 2.05ms	remaining: 850ms
1:	learn: 0.5952370	total: 4.38ms	remaining: 905ms
2:	learn: 0.5673943	total: 6.41ms	remaining: 881ms
3:	learn: 0.5227326	total: 8.13ms	remaining: 835ms
4:	learn: 0.4887439	total: 9.74ms	remaining: 799ms
5:	learn: 0.4533254	total: 11.5ms	remaining: 781ms
6:	learn: 0.4281889	total: 13.1ms	remaining: 763ms
7:	learn: 0.3984210	total: 14.7ms	remaining: 748ms
8:	learn: 0.3752295	total: 16.4ms	remaining: 740ms
9:	learn: 0.3463209	total: 32.2ms	remaining: 1.3s
10:	learn: 0.3264916	total: 34ms	remaining: 1.25s
11:	learn: 0.3112848	total: 35.7ms	remaining: 1.2s
12:	learn: 0.2874346	total: 37.5ms	remaining: 1.16s
13:	learn: 0.2695143	total: 39.5ms	remaining: 1.13s
14:	learn: 0.2534496	total: 41.3ms	remaining: 1.1s
15:	learn: 0.2432291	total: 43.3ms	remaining: 1.08s
16:	learn: 0.2350590	total: 45.4ms	remaining: 1.06s
17:	learn: 0.2241566	total: 47.3ms	remaining: 1.04s
18:	learn: 0.2143400	total: 49.1ms	remaining: 1.02s
19:	learn: 0.2033556	total:

...

<ipython-input-75-de5c804e77b8>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 1.0),
<ipython-input-75-de5c804e77b8>:8: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'subsample': trial.suggest_loguniform('subsample', 0.01, 1.0)


0:	learn: 0.5590170	total: 9.61ms	remaining: 3s
1:	learn: 0.4453538	total: 13.6ms	remaining: 2.11s
2:	learn: 0.3601204	total: 17.2ms	remaining: 1.78s
3:	learn: 0.2924259	total: 20.7ms	remaining: 1.6s
4:	learn: 0.2493662	total: 24.8ms	remaining: 1.53s
5:	learn: 0.2132384	total: 28.5ms	remaining: 1.46s
6:	learn: 0.1888567	total: 32.1ms	remaining: 1.4s
7:	learn: 0.1658753	total: 35.7ms	remaining: 1.36s
8:	learn: 0.1462099	total: 39.7ms	remaining: 1.34s
9:	learn: 0.1339625	total: 43.6ms	remaining: 1.32s
10:	learn: 0.1209445	total: 47.2ms	remaining: 1.3s
11:	learn: 0.1105349	total: 50.9ms	remaining: 1.28s
12:	learn: 0.1020531	total: 54.8ms	remaining: 1.26s
13:	learn: 0.0951033	total: 58.6ms	remaining: 1.25s
14:	learn: 0.0885680	total: 62.2ms	remaining: 1.24s
15:	learn: 0.0828827	total: 65.8ms	remaining: 1.22s
16:	learn: 0.0771338	total: 69.6ms	remaining: 1.21s
17:	learn: 0.0729277	total: 73.4ms	remaining: 1.2s
18:	learn: 0.0697457	total: 77.1ms	remaining: 1.19s
19:	learn: 0.0666389	total: 8

182:	learn: 0.0092615	total: 747ms	remaining: 531ms
183:	learn: 0.0091596	total: 751ms	remaining: 527ms
184:	learn: 0.0091184	total: 755ms	remaining: 522ms
185:	learn: 0.0090878	total: 759ms	remaining: 519ms
186:	learn: 0.0089755	total: 763ms	remaining: 514ms
187:	learn: 0.0089635	total: 768ms	remaining: 510ms
188:	learn: 0.0089487	total: 772ms	remaining: 506ms
189:	learn: 0.0088593	total: 776ms	remaining: 502ms
190:	learn: 0.0088521	total: 779ms	remaining: 498ms
191:	learn: 0.0088041	total: 783ms	remaining: 494ms
192:	learn: 0.0086864	total: 787ms	remaining: 489ms
193:	learn: 0.0086255	total: 791ms	remaining: 485ms
194:	learn: 0.0085909	total: 794ms	remaining: 481ms
195:	learn: 0.0085798	total: 798ms	remaining: 476ms
196:	learn: 0.0085649	total: 802ms	remaining: 472ms
197:	learn: 0.0083982	total: 806ms	remaining: 468ms
198:	learn: 0.0083845	total: 810ms	remaining: 464ms
199:	learn: 0.0083845	total: 813ms	remaining: 460ms
200:	learn: 0.0083428	total: 817ms	remaining: 455ms
201:	learn: 

[I 2023-08-13 14:07:57,645] Trial 99 finished with value: 0.4905362776025236 and parameters: {'max_depth': 7, 'learning_rate': 0.07200431936748011, 'n_estimators': 313, 'subsample': 0.27151827926459865}. Best is trial 96 with value: 0.7413249211356466.


282:	learn: 0.0052436	total: 1.13s	remaining: 119ms
283:	learn: 0.0052117	total: 1.13s	remaining: 116ms
284:	learn: 0.0052042	total: 1.14s	remaining: 112ms
285:	learn: 0.0051813	total: 1.14s	remaining: 108ms
286:	learn: 0.0051790	total: 1.14s	remaining: 104ms
287:	learn: 0.0051191	total: 1.15s	remaining: 99.6ms
288:	learn: 0.0051051	total: 1.15s	remaining: 95.6ms
289:	learn: 0.0050664	total: 1.16s	remaining: 91.6ms
290:	learn: 0.0050380	total: 1.16s	remaining: 87.7ms
291:	learn: 0.0049829	total: 1.16s	remaining: 83.7ms
292:	learn: 0.0049829	total: 1.17s	remaining: 79.6ms
293:	learn: 0.0049633	total: 1.17s	remaining: 75.6ms
294:	learn: 0.0049300	total: 1.17s	remaining: 71.6ms
295:	learn: 0.0049064	total: 1.18s	remaining: 67.6ms
296:	learn: 0.0048554	total: 1.18s	remaining: 63.7ms
297:	learn: 0.0048475	total: 1.19s	remaining: 59.7ms
298:	learn: 0.0048357	total: 1.19s	remaining: 55.7ms
299:	learn: 0.0048357	total: 1.19s	remaining: 51.7ms
300:	learn: 0.0048232	total: 1.2s	remaining: 47.7ms

In [72]:
def objective(trial):
    """Define the objective function"""

    params = {
        'max_depth': trial.suggest_int('max_depth', 1, 9),
        'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 1.0),
        'n_estimators': trial.suggest_int('n_estimators', 50, 500),
        'subsample': trial.suggest_loguniform('subsample', 0.01, 1.0)
    }

    # Fit the model
    optuna_model =XGBClassifier(**params)
    optuna_model.fit(X_train, y_train)

    # Make predictions
    y_pred = optuna_model.predict(X_test)

    # Evaluate predictions
    roc_auc = roc_auc_score(y_test, y_pred)
    return roc_auc

In [83]:
study_XGBClassifier = optuna.create_study(direction='maximize')
study_XGBClassifier.optimize(objective, n_trials=100)

print('Number of finished trials: {}'.format(len(study_XGBClassifier.trials)))
print('Best trial XGBClassifier:')
trial = study_XGBClassifier.best_trial

print('  Value: {}'.format(trial.value))
print('  Params: ')

for key, value in trial.params.items():
    print('    {}: {}'.format(key, value))

[I 2023-08-13 14:08:30,293] A new study created in memory with name: no-name-30355aa8-35f3-4a72-92fc-8c7a06a1a514
<ipython-input-75-de5c804e77b8>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 1.0),
<ipython-input-75-de5c804e77b8>:8: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'subsample': trial.suggest_loguniform('subsample', 0.01, 1.0)


0:	learn: 0.6064786	total: 12.4ms	remaining: 4.38s
1:	learn: 0.5503655	total: 13.9ms	remaining: 2.44s
2:	learn: 0.4792975	total: 15.1ms	remaining: 1.76s
3:	learn: 0.4211894	total: 16.2ms	remaining: 1.42s
4:	learn: 0.3795539	total: 17.5ms	remaining: 1.22s
5:	learn: 0.3306589	total: 18.7ms	remaining: 1.08s
6:	learn: 0.2818163	total: 19.9ms	remaining: 982ms
7:	learn: 0.2499632	total: 21.1ms	remaining: 909ms
8:	learn: 0.2233931	total: 22.3ms	remaining: 852ms
9:	learn: 0.2085774	total: 23.5ms	remaining: 807ms
10:	learn: 0.1979067	total: 24.7ms	remaining: 767ms
11:	learn: 0.1932149	total: 26.3ms	remaining: 748ms
12:	learn: 0.1788231	total: 28.4ms	remaining: 741ms
13:	learn: 0.1727320	total: 29.7ms	remaining: 720ms
14:	learn: 0.1650336	total: 31.1ms	remaining: 700ms
15:	learn: 0.1596395	total: 32.4ms	remaining: 682ms
16:	learn: 0.1509839	total: 34ms	remaining: 673ms
17:	learn: 0.1502042	total: 35.4ms	remaining: 659ms
18:	learn: 0.1447237	total: 36.6ms	remaining: 644ms
19:	learn: 0.1385179	tot

[I 2023-08-13 14:08:30,890] Trial 0 finished with value: 0.5 and parameters: {'max_depth': 3, 'learning_rate': 0.0657123752580358, 'n_estimators': 353, 'subsample': 0.014973146038075065}. Best is trial 0 with value: 0.5.


288:	learn: 0.0546053	total: 368ms	remaining: 81.5ms
289:	learn: 0.0545116	total: 369ms	remaining: 80.3ms
290:	learn: 0.0544763	total: 371ms	remaining: 79ms
291:	learn: 0.0543582	total: 372ms	remaining: 77.7ms
292:	learn: 0.0537038	total: 373ms	remaining: 76.5ms
293:	learn: 0.0537038	total: 375ms	remaining: 75.2ms
294:	learn: 0.0536391	total: 376ms	remaining: 73.9ms
295:	learn: 0.0534998	total: 377ms	remaining: 72.6ms
296:	learn: 0.0534622	total: 378ms	remaining: 71.3ms
297:	learn: 0.0534294	total: 380ms	remaining: 70.1ms
298:	learn: 0.0533582	total: 381ms	remaining: 68.9ms
299:	learn: 0.0533128	total: 383ms	remaining: 67.6ms
300:	learn: 0.0532383	total: 384ms	remaining: 66.4ms
301:	learn: 0.0531854	total: 385ms	remaining: 65.1ms
302:	learn: 0.0531611	total: 387ms	remaining: 63.8ms
303:	learn: 0.0530302	total: 388ms	remaining: 62.5ms
304:	learn: 0.0530065	total: 389ms	remaining: 61.2ms
305:	learn: 0.0529629	total: 390ms	remaining: 59.9ms
306:	learn: 0.0528761	total: 391ms	remaining: 58

<ipython-input-75-de5c804e77b8>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 1.0),
<ipython-input-75-de5c804e77b8>:8: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'subsample': trial.suggest_loguniform('subsample', 0.01, 1.0)


...

0:	learn: 0.5310011	total: 18.1ms	remaining: 3.07s
1:	learn: 0.4208225	total: 33.4ms	remaining: 2.81s
2:	learn: 0.3347440	total: 49.3ms	remaining: 2.74s
3:	learn: 0.2795510	total: 64.3ms	remaining: 2.67s
4:	learn: 0.2315132	total: 79.3ms	remaining: 2.62s
5:	learn: 0.1947004	total: 96.3ms	remaining: 2.63s
6:	learn: 0.1693972	total: 114ms	remaining: 2.65s
7:	learn: 0.1429168	total: 131ms	remaining: 2.65s
8:	learn: 0.1242872	total: 146ms	remaining: 2.62s
9:	learn: 0.1099724	total: 162ms	remaining: 2.59s
10:	learn: 0.0965142	total: 178ms	remaining: 2.58s
11:	learn: 0.0866480	total: 195ms	remaining: 2.57s
12:	learn: 0.0780177	total: 212ms	remaining: 2.56s
13:	learn: 0.0721793	total: 230ms	remaining: 2.57s
14:	learn: 0.0666536	total: 248ms	remaining: 2.56s
15:	learn: 0.0618853	total: 263ms	remaining: 2.53s
16:	learn: 0.0575782	total: 278ms	remaining: 2.5s
17:	learn: 0.0539928	total: 293ms	remaining: 2.48s
18:	learn: 0.0502132	total: 310ms	remaining: 2.47s
19:	learn: 0.0472842	total: 327ms	re

[I 2023-08-13 14:12:05,625] Trial 98 finished with value: 0.7145110410094637 and parameters: {'max_depth': 9, 'learning_rate': 0.08996565424755372, 'n_estimators': 170, 'subsample': 0.5495273937727488}. Best is trial 43 with value: 0.8406940063091483.
<ipython-input-75-de5c804e77b8>:6: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'learning_rate': trial.suggest_loguniform('learning_rate', 0.01, 1.0),
<ipython-input-75-de5c804e77b8>:8: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  'subsample': trial.suggest_loguniform('subsample', 0.01, 1.0)


0:	learn: 0.5390408	total: 16.4ms	remaining: 2.34s
1:	learn: 0.4324199	total: 30.6ms	remaining: 2.17s
2:	learn: 0.3472693	total: 45.2ms	remaining: 2.13s
3:	learn: 0.2920680	total: 59.1ms	remaining: 2.07s
4:	learn: 0.2414537	total: 73.2ms	remaining: 2.04s
5:	learn: 0.2042752	total: 88.8ms	remaining: 2.04s
6:	learn: 0.1784075	total: 104ms	remaining: 2.03s
7:	learn: 0.1515082	total: 118ms	remaining: 2s
8:	learn: 0.1326667	total: 133ms	remaining: 1.99s
9:	learn: 0.1175548	total: 149ms	remaining: 2s
10:	learn: 0.1033856	total: 165ms	remaining: 1.99s
11:	learn: 0.0933355	total: 180ms	remaining: 1.98s
12:	learn: 0.0833005	total: 194ms	remaining: 1.95s
13:	learn: 0.0763314	total: 210ms	remaining: 1.95s
14:	learn: 0.0707640	total: 226ms	remaining: 1.94s
15:	learn: 0.0663132	total: 241ms	remaining: 1.93s
16:	learn: 0.0616810	total: 256ms	remaining: 1.91s
17:	learn: 0.0580347	total: 270ms	remaining: 1.89s
18:	learn: 0.0537764	total: 284ms	remaining: 1.87s
19:	learn: 0.0508484	total: 299ms	remaini

[I 2023-08-13 14:12:07,950] Trial 99 finished with value: 0.638801261829653 and parameters: {'max_depth': 9, 'learning_rate': 0.08494842392100611, 'n_estimators': 144, 'subsample': 0.5356958582739644}. Best is trial 43 with value: 0.8406940063091483.


138:	learn: 0.0058984	total: 2.08s	remaining: 74.9ms
139:	learn: 0.0058402	total: 2.1s	remaining: 59.9ms
140:	learn: 0.0058250	total: 2.11s	remaining: 44.9ms
141:	learn: 0.0057464	total: 2.13s	remaining: 29.9ms
142:	learn: 0.0057324	total: 2.14s	remaining: 15ms
143:	learn: 0.0056536	total: 2.15s	remaining: 0us
Number of finished trials: 100
Best trial XGBClassifier:
  Value: 0.8406940063091483
  Params: 
    max_depth: 9
    learning_rate: 0.14492755662720488
    n_estimators: 245
    subsample: 0.8324189235832102


## Результаты после подборки гиперпараметров с помощью optuna

LGBMClassifier:
  Value: 0.7381703470031546

 CatBoostClassifier:
  Value: 0.7965299684542586
  
GradientBoostingClassifier:
  Value: 0.7413249211356466 
  
XGBClassifier:
  Value: 0.8406940063091483  

## Сравним полученные результаты:

После обучение без подборки гиперпараметров - Самый высокий показатель roc_auc_score получил GradientBoostingClassifier с показателем = 0.78

При обучении с подбором гиперпараметров с помощью optuna - наиысший показатель был получен при помощи XGBClassifier с roc_auc_score = 0.84